In [12]:
import pandas as pd

# Load the CSV file
file_path = '/Users/wenjing/Downloads/Capstone/10_stocks_filtered_scored.csv'
df = pd.read_csv(file_path)

# Select only the required columns
filtered_df = df[['Date', 'Stock_symbol', 'sentiment_label', 'sentiment_score']]

# Display the filtered DataFrame
print(filtered_df.head())

# Optionally, save the filtered DataFrame to a new CSV file
output_path = '/Users/wenjing/Downloads/Capstone/filtered_sentiment_data.csv'
filtered_df.to_csv(output_path, index=False)


                      Date Stock_symbol sentiment_label  sentiment_score
0  2023-12-16 22:00:00 UTC         AAPL        positive         0.589453
1  2023-12-16 22:00:00 UTC         AAPL         neutral         0.898743
2  2023-12-16 21:00:00 UTC         AAPL        negative         0.972591
3  2023-12-16 21:00:00 UTC         AAPL         neutral         0.938853
4  2023-12-16 21:00:00 UTC         AAPL         neutral         0.523862


In [3]:
import pandas as pd

# Load the CSV file
file_path = '/Users/wenjing/Downloads/Capstone/filtered_sentiment_data.csv'
df = pd.read_csv(file_path)

# Define a function to calculate the count and mean for each sentiment label
def sentiment_aggregates(sub_df):
    return {
        'sentiment_label_positive_count': (sub_df['sentiment_label'] == 'positive').sum(),
        'sentiment_score_positive': sub_df.loc[sub_df['sentiment_label'] == 'positive', 'sentiment_score'].mean(),
        'sentiment_label_negative_count': (sub_df['sentiment_label'] == 'negative').sum(),
        'sentiment_score_negative': sub_df.loc[sub_df['sentiment_label'] == 'negative', 'sentiment_score'].mean(),
        'sentiment_label_neutral_count': (sub_df['sentiment_label'] == 'neutral').sum(),
        'sentiment_score_neutral': sub_df.loc[sub_df['sentiment_label'] == 'neutral', 'sentiment_score'].mean()
    }

# Group by Date and Stock_symbol and apply the aggregation function
result_df = df.groupby(['Date', 'Stock_symbol']).apply(sentiment_aggregates).apply(pd.Series).reset_index()

# Display the result
print(result_df.head(50))

# Optionally, save the result to a new CSV file
output_path = '/Users/wenjing/Downloads/Capstone/aggregated_sentiment_data.csv'
result_df.to_csv(output_path, index=False)


/var/folders/z8/1bf58b0x31xb_r9dnkm4w93c0000gn/T/ipykernel_81707/1787878070.py:19: DeprecationWarning: DataFrameGroupBy.apply operated on the grouping columns. This behavior is deprecated, and in a future version of pandas the grouping columns will be excluded from the operation. Either pass `include_groups=False` to exclude the groupings or explicitly select the grouping columns after groupby to silence this warning.
  result_df = df.groupby(['Date', 'Stock_symbol']).apply(sentiment_aggregates).apply(pd.Series).reset_index()


                       Date Stock_symbol  sentiment_label_positive_count  \
0   2009-11-04 00:00:00 UTC          MRK                             0.0   
1   2009-11-30 00:00:00 UTC          MRK                             0.0   
2   2009-12-02 00:00:00 UTC          MRK                             0.0   
3   2009-12-03 00:00:00 UTC          MRK                             0.0   
4   2009-12-06 00:00:00 UTC          MRK                             0.0   
5   2010-01-15 00:00:00 UTC          MRK                             1.0   
6   2010-02-11 00:00:00 UTC          MRK                             0.0   
7   2010-03-22 00:00:00 UTC          MRK                             0.0   
8   2010-04-19 00:00:00 UTC          MRK                             0.0   
9   2010-04-21 00:00:00 UTC          MRK                             1.0   
10  2010-04-22 00:00:00 UTC          MRK                             0.0   
11  2010-04-30 00:00:00 UTC          MRK                             0.0   
12  2010-05-

In [17]:
import pandas as pd
import os

# Load the sentiment data file (update path if necessary)
sentiment_data_path = '/Users/wenjing/Downloads/Capstone/aggregated_sentiment_data.csv'
sentiment_df = pd.read_csv(sentiment_data_path)

# Convert the Date column in sentiment data to datetime format and remove timezone
sentiment_df['Date'] = pd.to_datetime(sentiment_df['Date']).dt.tz_localize(None)

# Path to the full history and output directories
price_files_dir = '/Users/wenjing/Downloads/Capstone/full_history/'
output_dir = '/Users/wenjing/Downloads/Capstone/combined/'

# Ensure output directory exists
os.makedirs(output_dir, exist_ok=True)

# List of unique stock symbols in the sentiment data
stock_symbols = sentiment_df['Stock_symbol'].unique()

# Loop through each stock symbol and process its data
for symbol in stock_symbols:
    # Path to the price file for the current stock symbol
    price_file_path = os.path.join(price_files_dir, f'{symbol}.csv')
    
    # Check if the price file exists for the stock symbol
    if os.path.exists(price_file_path):
        # Load the price data for the current stock symbol
        price_df = pd.read_csv(price_file_path)
        
        # Rename and convert the date column in price data to a uniform format and remove timezone
        price_df.rename(columns={'date': 'Date'}, inplace=True)
        price_df['Date'] = pd.to_datetime(price_df['Date']).dt.tz_localize(None)
        
        # Filter the sentiment data for the current stock symbol
        sentiment_stock_df = sentiment_df[sentiment_df['Stock_symbol'] == symbol]
        
        # Merge the price data with the sentiment data on Date
        merged_df = pd.merge(price_df, sentiment_stock_df, how='left', on='Date')
        
        # Fill missing sentiment counts with 0 and sentiment scores with NaN
        merged_df['sentiment_label_positive_count'].fillna(0, inplace=True)
        merged_df['sentiment_score_positive'].fillna(float('nan'), inplace=True)
        merged_df['sentiment_label_negative_count'].fillna(0, inplace=True)
        merged_df['sentiment_score_negative'].fillna(float('nan'), inplace=True)
        merged_df['sentiment_label_neutral_count'].fillna(0, inplace=True)
        merged_df['sentiment_score_neutral'].fillna(float('nan'), inplace=True)
        
        # Save the combined DataFrame to a new CSV file
        output_path = os.path.join(output_dir, f'{symbol}.csv')
        merged_df.to_csv(output_path, index=False)
        
        print(f'Saved combined data for {symbol} to {output_path}')
    else:
        print(f'Price file for {symbol} not found. Skipping...')



/var/folders/z8/1bf58b0x31xb_r9dnkm4w93c0000gn/T/ipykernel_81707/3182346920.py:42: FutureWarning: A value is trying to be set on a copy of a DataFrame or Series through chained assignment using an inplace method.
The behavior will change in pandas 3.0. This inplace method will never work because the intermediate object on which we are setting values always behaves as a copy.

For example, when doing 'df[col].method(value, inplace=True)', try using 'df.method({col: value}, inplace=True)' or df[col] = df[col].method(value) instead, to perform the operation inplace on the original object.


  merged_df['sentiment_label_positive_count'].fillna(0, inplace=True)
/var/folders/z8/1bf58b0x31xb_r9dnkm4w93c0000gn/T/ipykernel_81707/3182346920.py:43: FutureWarning: A value is trying to be set on a copy of a DataFrame or Series through chained assignment using an inplace method.
The behavior will change in pandas 3.0. This inplace method will never work because the intermediate object on which we ar

Saved combined data for MRK to /Users/wenjing/Downloads/Capstone/combined/MRK.csv
Saved combined data for AMD to /Users/wenjing/Downloads/Capstone/combined/AMD.csv
Saved combined data for INTC to /Users/wenjing/Downloads/Capstone/combined/INTC.csv


/var/folders/z8/1bf58b0x31xb_r9dnkm4w93c0000gn/T/ipykernel_81707/3182346920.py:42: FutureWarning: A value is trying to be set on a copy of a DataFrame or Series through chained assignment using an inplace method.
The behavior will change in pandas 3.0. This inplace method will never work because the intermediate object on which we are setting values always behaves as a copy.

For example, when doing 'df[col].method(value, inplace=True)', try using 'df.method({col: value}, inplace=True)' or df[col] = df[col].method(value) instead, to perform the operation inplace on the original object.


  merged_df['sentiment_label_positive_count'].fillna(0, inplace=True)
/var/folders/z8/1bf58b0x31xb_r9dnkm4w93c0000gn/T/ipykernel_81707/3182346920.py:43: FutureWarning: A value is trying to be set on a copy of a DataFrame or Series through chained assignment using an inplace method.
The behavior will change in pandas 3.0. This inplace method will never work because the intermediate object on which we ar

Saved combined data for BA to /Users/wenjing/Downloads/Capstone/combined/BA.csv
Saved combined data for GOOG to /Users/wenjing/Downloads/Capstone/combined/GOOG.csv
Saved combined data for NVDA to /Users/wenjing/Downloads/Capstone/combined/NVDA.csv
Saved combined data for MSFT to /Users/wenjing/Downloads/Capstone/combined/MSFT.csv
Saved combined data for TSLA to /Users/wenjing/Downloads/Capstone/combined/TSLA.csv
Saved combined data for AAPL to /Users/wenjing/Downloads/Capstone/combined/AAPL.csv


/var/folders/z8/1bf58b0x31xb_r9dnkm4w93c0000gn/T/ipykernel_81707/3182346920.py:42: FutureWarning: A value is trying to be set on a copy of a DataFrame or Series through chained assignment using an inplace method.
The behavior will change in pandas 3.0. This inplace method will never work because the intermediate object on which we are setting values always behaves as a copy.

For example, when doing 'df[col].method(value, inplace=True)', try using 'df.method({col: value}, inplace=True)' or df[col] = df[col].method(value) instead, to perform the operation inplace on the original object.


  merged_df['sentiment_label_positive_count'].fillna(0, inplace=True)
/var/folders/z8/1bf58b0x31xb_r9dnkm4w93c0000gn/T/ipykernel_81707/3182346920.py:43: FutureWarning: A value is trying to be set on a copy of a DataFrame or Series through chained assignment using an inplace method.
The behavior will change in pandas 3.0. This inplace method will never work because the intermediate object on which we ar

In [18]:
import pandas as pd
import os

# Path to the combined directory
combined_dir = '/Users/wenjing/Downloads/Capstone/combined/'
output_dir = '/Users/wenjing/Downloads/Capstone/filtered/'

# Ensure output directory exists
os.makedirs(output_dir, exist_ok=True)

# Iterate through each file in the combined directory
for filename in os.listdir(combined_dir):
    if filename.endswith('.csv'):
        # Load the CSV file
        file_path = os.path.join(combined_dir, filename)
        df = pd.read_csv(file_path)

        # Convert Date column to datetime
        df['Date'] = pd.to_datetime(df['Date'])

        # Determine the minimum and maximum dates where Stock_symbol is not NaN
        min_date = df.loc[df['Stock_symbol'].notna(), 'Date'].min()
        max_date = df.loc[df['Stock_symbol'].notna(), 'Date'].max()

        # Filter the DataFrame to keep only rows within this date range
        filtered_df = df[(df['Date'] >= min_date) & (df['Date'] <= max_date)]

        # Reset index for a cleaner DataFrame
        filtered_df = filtered_df.reset_index(drop=True)

        # Save the filtered DataFrame to the output directory
        output_path = os.path.join(output_dir, filename)
        filtered_df.to_csv(output_path, index=False)

        print(f'Saved filtered data for {filename} to {output_path}')


Saved filtered data for BA.csv to /Users/wenjing/Downloads/Capstone/filtered/BA.csv
Saved filtered data for MRK.csv to /Users/wenjing/Downloads/Capstone/filtered/MRK.csv
Saved filtered data for INTC.csv to /Users/wenjing/Downloads/Capstone/filtered/INTC.csv
Saved filtered data for MSFT.csv to /Users/wenjing/Downloads/Capstone/filtered/MSFT.csv
Saved filtered data for AMD.csv to /Users/wenjing/Downloads/Capstone/filtered/AMD.csv
Saved filtered data for NVDA.csv to /Users/wenjing/Downloads/Capstone/filtered/NVDA.csv
Saved filtered data for TSLA.csv to /Users/wenjing/Downloads/Capstone/filtered/TSLA.csv
Saved filtered data for GOOG.csv to /Users/wenjing/Downloads/Capstone/filtered/GOOG.csv
Saved filtered data for AAPL.csv to /Users/wenjing/Downloads/Capstone/filtered/AAPL.csv


In [23]:
import pandas as pd
import numpy as np
import os
from statsmodels.tsa.statespace.sarimax import SARIMAX
from sklearn.metrics import mean_squared_error
from itertools import product

# Define paths
filtered_dir = '/Users/wenjing/Downloads/Capstone/filtered/'

# Function to evaluate SARIMAX models
def evaluate_sarimax(train, test, exog_train=None, exog_test=None, order=(1, 1, 1)):
    model = SARIMAX(train, exog=exog_train, order=order, enforce_stationarity=False, enforce_invertibility=False)
    model_fit = model.fit(disp=False)
    predictions = model_fit.predict(start=len(train), end=len(train) + len(test) - 1, exog=exog_test)
    rmse = mean_squared_error(test, predictions, squared=False)
    return rmse, model_fit

# Prepare lists to store results
results = []

# Parameter grid for ARIMA
p = d = q = range(0, 6)
pdq = list(product(p, d, q))

# Iterate through each file in the filtered directory
for filename in os.listdir(filtered_dir):
    print(filename)
    if filename.endswith('.csv'):
        # Load the data
        file_path = os.path.join(filtered_dir, filename)
        df = pd.read_csv(file_path)

        # Convert Date column to datetime and sort by Date
        df['Date'] = pd.to_datetime(df['Date'])
        df = df.sort_values(by='Date').reset_index(drop=True)
        
        # Fill NaN in sentiment_score columns with zero
        sentiment_columns = [
            'sentiment_label_positive_count', 'sentiment_score_positive',
            'sentiment_label_negative_count', 'sentiment_score_negative',
            'sentiment_label_neutral_count', 'sentiment_score_neutral'
        ]
        df[sentiment_columns] = df[sentiment_columns].fillna(0)

        # Define features and target
        target = 'close'
        features_with_sentiment = ['open', 'volume'] + sentiment_columns
        features_without_sentiment = ['open', 'volume']

        # Prepare training and test datasets
        train_size = int(len(df) * 0.8)
        train, test = df[target][:train_size], df[target][train_size:]
        exog_train_with = df[features_with_sentiment][:train_size]
        exog_test_with = df[features_with_sentiment][train_size:]
        exog_train_without = df[features_without_sentiment][:train_size]
        exog_test_without = df[features_without_sentiment][train_size:]

        # Grid search for best SARIMAX parameters (with sentiment features)
        best_rmse_with = float("inf")
        best_order_with = None
        for param in pdq:
            try:
                rmse, _ = evaluate_sarimax(train, test, exog_train=exog_train_with, exog_test=exog_test_with, order=param)
                if rmse < best_rmse_with:
                    best_rmse_with = rmse
                    best_order_with = param
            except:
                continue

        # Grid search for best SARIMAX parameters (without sentiment features)
        best_rmse_without = float("inf")
        best_order_without = None
        for param in pdq:
            try:
                rmse, _ = evaluate_sarimax(train, test, exog_train=exog_train_without, exog_test=exog_test_without, order=param)
                if rmse < best_rmse_without:
                    best_rmse_without = rmse
                    best_order_without = param
            except:
                continue

        # Append results for this file
        results.append({
            'filename': filename,
            'best_rmse_with_sentiment': best_rmse_with,
            'best_order_with_sentiment': best_order_with,
            'best_rmse_without_sentiment': best_rmse_without,
            'best_order_without_sentiment': best_order_without
        })

# Display the results
results_df = pd.DataFrame(results)
print(results_df)


BA.csv


/Users/wenjing/miniforge3/envs/w210/lib/python3.9/site-packages/statsmodels/base/model.py:607: ConvergenceWarning: Maximum Likelihood optimization failed to converge. Check mle_retvals
  warnings.warn("Maximum Likelihood optimization failed to "
/Users/wenjing/miniforge3/envs/w210/lib/python3.9/site-packages/sklearn/metrics/_regression.py:492: FutureWarning: 'squared' is deprecated in version 1.4 and will be removed in 1.6. To calculate the root mean squared error, use the function'root_mean_squared_error'.
  warnings.warn(
/Users/wenjing/miniforge3/envs/w210/lib/python3.9/site-packages/statsmodels/base/model.py:607: ConvergenceWarning: Maximum Likelihood optimization failed to converge. Check mle_retvals
  warnings.warn("Maximum Likelihood optimization failed to "
/Users/wenjing/miniforge3/envs/w210/lib/python3.9/site-packages/sklearn/metrics/_regression.py:492: FutureWarning: 'squared' is deprecated in version 1.4 and will be removed in 1.6. To calculate the root mean squared error, 

/Users/wenjing/miniforge3/envs/w210/lib/python3.9/site-packages/statsmodels/base/model.py:607: ConvergenceWarning: Maximum Likelihood optimization failed to converge. Check mle_retvals
  warnings.warn("Maximum Likelihood optimization failed to "
/Users/wenjing/miniforge3/envs/w210/lib/python3.9/site-packages/sklearn/metrics/_regression.py:492: FutureWarning: 'squared' is deprecated in version 1.4 and will be removed in 1.6. To calculate the root mean squared error, use the function'root_mean_squared_error'.
  warnings.warn(
/Users/wenjing/miniforge3/envs/w210/lib/python3.9/site-packages/statsmodels/base/model.py:607: ConvergenceWarning: Maximum Likelihood optimization failed to converge. Check mle_retvals
  warnings.warn("Maximum Likelihood optimization failed to "
/Users/wenjing/miniforge3/envs/w210/lib/python3.9/site-packages/sklearn/metrics/_regression.py:492: FutureWarning: 'squared' is deprecated in version 1.4 and will be removed in 1.6. To calculate the root mean squared error, 

/Users/wenjing/miniforge3/envs/w210/lib/python3.9/site-packages/statsmodels/base/model.py:607: ConvergenceWarning: Maximum Likelihood optimization failed to converge. Check mle_retvals
  warnings.warn("Maximum Likelihood optimization failed to "
/Users/wenjing/miniforge3/envs/w210/lib/python3.9/site-packages/sklearn/metrics/_regression.py:492: FutureWarning: 'squared' is deprecated in version 1.4 and will be removed in 1.6. To calculate the root mean squared error, use the function'root_mean_squared_error'.
  warnings.warn(
/Users/wenjing/miniforge3/envs/w210/lib/python3.9/site-packages/statsmodels/base/model.py:607: ConvergenceWarning: Maximum Likelihood optimization failed to converge. Check mle_retvals
  warnings.warn("Maximum Likelihood optimization failed to "
/Users/wenjing/miniforge3/envs/w210/lib/python3.9/site-packages/sklearn/metrics/_regression.py:492: FutureWarning: 'squared' is deprecated in version 1.4 and will be removed in 1.6. To calculate the root mean squared error, 

/Users/wenjing/miniforge3/envs/w210/lib/python3.9/site-packages/statsmodels/base/model.py:607: ConvergenceWarning: Maximum Likelihood optimization failed to converge. Check mle_retvals
  warnings.warn("Maximum Likelihood optimization failed to "
/Users/wenjing/miniforge3/envs/w210/lib/python3.9/site-packages/sklearn/metrics/_regression.py:492: FutureWarning: 'squared' is deprecated in version 1.4 and will be removed in 1.6. To calculate the root mean squared error, use the function'root_mean_squared_error'.
  warnings.warn(
/Users/wenjing/miniforge3/envs/w210/lib/python3.9/site-packages/statsmodels/base/model.py:607: ConvergenceWarning: Maximum Likelihood optimization failed to converge. Check mle_retvals
  warnings.warn("Maximum Likelihood optimization failed to "
/Users/wenjing/miniforge3/envs/w210/lib/python3.9/site-packages/sklearn/metrics/_regression.py:492: FutureWarning: 'squared' is deprecated in version 1.4 and will be removed in 1.6. To calculate the root mean squared error, 

...

/Users/wenjing/miniforge3/envs/w210/lib/python3.9/site-packages/statsmodels/base/model.py:607: ConvergenceWarning: Maximum Likelihood optimization failed to converge. Check mle_retvals
  warnings.warn("Maximum Likelihood optimization failed to "
/Users/wenjing/miniforge3/envs/w210/lib/python3.9/site-packages/sklearn/metrics/_regression.py:492: FutureWarning: 'squared' is deprecated in version 1.4 and will be removed in 1.6. To calculate the root mean squared error, use the function'root_mean_squared_error'.
  warnings.warn(
/Users/wenjing/miniforge3/envs/w210/lib/python3.9/site-packages/statsmodels/base/model.py:607: ConvergenceWarning: Maximum Likelihood optimization failed to converge. Check mle_retvals
  warnings.warn("Maximum Likelihood optimization failed to "
/Users/wenjing/miniforge3/envs/w210/lib/python3.9/site-packages/sklearn/metrics/_regression.py:492: FutureWarning: 'squared' is deprecated in version 1.4 and will be removed in 1.6. To calculate the root mean squared error, 

/Users/wenjing/miniforge3/envs/w210/lib/python3.9/site-packages/statsmodels/base/model.py:607: ConvergenceWarning: Maximum Likelihood optimization failed to converge. Check mle_retvals
  warnings.warn("Maximum Likelihood optimization failed to "
/Users/wenjing/miniforge3/envs/w210/lib/python3.9/site-packages/sklearn/metrics/_regression.py:492: FutureWarning: 'squared' is deprecated in version 1.4 and will be removed in 1.6. To calculate the root mean squared error, use the function'root_mean_squared_error'.
  warnings.warn(
/Users/wenjing/miniforge3/envs/w210/lib/python3.9/site-packages/statsmodels/base/model.py:607: ConvergenceWarning: Maximum Likelihood optimization failed to converge. Check mle_retvals
  warnings.warn("Maximum Likelihood optimization failed to "
/Users/wenjing/miniforge3/envs/w210/lib/python3.9/site-packages/sklearn/metrics/_regression.py:492: FutureWarning: 'squared' is deprecated in version 1.4 and will be removed in 1.6. To calculate the root mean squared error, 

/Users/wenjing/miniforge3/envs/w210/lib/python3.9/site-packages/statsmodels/base/model.py:607: ConvergenceWarning: Maximum Likelihood optimization failed to converge. Check mle_retvals
  warnings.warn("Maximum Likelihood optimization failed to "
/Users/wenjing/miniforge3/envs/w210/lib/python3.9/site-packages/sklearn/metrics/_regression.py:492: FutureWarning: 'squared' is deprecated in version 1.4 and will be removed in 1.6. To calculate the root mean squared error, use the function'root_mean_squared_error'.
  warnings.warn(
/Users/wenjing/miniforge3/envs/w210/lib/python3.9/site-packages/statsmodels/base/model.py:607: ConvergenceWarning: Maximum Likelihood optimization failed to converge. Check mle_retvals
  warnings.warn("Maximum Likelihood optimization failed to "
/Users/wenjing/miniforge3/envs/w210/lib/python3.9/site-packages/sklearn/metrics/_regression.py:492: FutureWarning: 'squared' is deprecated in version 1.4 and will be removed in 1.6. To calculate the root mean squared error, 

   filename  best_rmse_with_sentiment best_order_with_sentiment  \
0    BA.csv                  3.169362                 (0, 0, 0)   
1   MRK.csv                  1.003401                 (4, 0, 4)   
2  INTC.csv                  0.691238                 (2, 0, 3)   
3  MSFT.csv                  4.168789                 (0, 0, 5)   
4   AMD.csv                  2.475428                 (3, 0, 5)   
5  NVDA.csv                  9.831670                 (4, 0, 5)   
6  TSLA.csv                  5.842376                 (4, 0, 3)   
7  GOOG.csv                  1.965512                 (3, 0, 3)   
8  AAPL.csv                  1.952407                 (0, 0, 2)   

   best_rmse_without_sentiment best_order_without_sentiment  
0                     3.109099                    (0, 0, 0)  
1                     1.009790                    (0, 0, 1)  
2                     0.713546                    (2, 0, 3)  
3                     4.248414                    (0, 0, 5)  
4                  

/Users/wenjing/miniforge3/envs/w210/lib/python3.9/site-packages/statsmodels/base/model.py:607: ConvergenceWarning: Maximum Likelihood optimization failed to converge. Check mle_retvals
  warnings.warn("Maximum Likelihood optimization failed to "
/Users/wenjing/miniforge3/envs/w210/lib/python3.9/site-packages/sklearn/metrics/_regression.py:492: FutureWarning: 'squared' is deprecated in version 1.4 and will be removed in 1.6. To calculate the root mean squared error, use the function'root_mean_squared_error'.
  warnings.warn(


In [20]:
results_df

filename  best_rmse_with_sentiment best_order_with_sentiment  \
0    BA.csv                  3.169362                 (0, 0, 0)   
1   MRK.csv                  1.003406                 (0, 0, 1)   
2  INTC.csv                  0.691809                 (1, 0, 1)   
3  MSFT.csv                  4.181366                 (0, 0, 0)   
4   AMD.csv                  2.475781                 (0, 0, 0)   
5  NVDA.csv                  9.845459                 (1, 0, 0)   
6  TSLA.csv                  5.848536                 (1, 0, 1)   
7  GOOG.csv                  1.971344                 (1, 0, 1)   
8  AAPL.csv                  1.952956                 (0, 0, 0)   

   best_rmse_without_sentiment best_order_without_sentiment  
0                     3.109099                    (0, 0, 0)  
1                     1.009790                    (0, 0, 1)  
2                     0.714006                    (0, 0, 1)  
3                     4.261750                    (1, 0, 0)  
4                     2.487848                    (0, 0, 0)  
5                     9.898564                    (0, 0, 1)  
6                     6.015946                    (1, 0, 1)  
7                     1.681465                    (0, 0, 1)  
8                     1.873778                    (0, 0, 1)

In [21]:
import pandas as pd
import numpy as np
import os
from statsmodels.tsa.statespace.sarimax import SARIMAX
from sklearn.metrics import mean_squared_error
from itertools import product
from statsmodels.tsa.stattools import adfuller

# Define paths
filtered_dir = '/Users/wenjing/Downloads/Capstone/filtered/'

# Function to evaluate SARIMAX models
def evaluate_sarimax(train, test, exog_train=None, exog_test=None, order=(1, 1, 1)):
    model = SARIMAX(train, exog=exog_train, order=order, enforce_stationarity=False, enforce_invertibility=False)
    model_fit = model.fit(disp=False)
    predictions = model_fit.predict(start=len(train), end=len(train) + len(test) - 1, exog=exog_test)
    rmse = mean_squared_error(test, predictions, squared=False)
    return rmse, model_fit

# Function to determine the optimal differencing order (d) with ADF test
def get_differencing_order(series):
    d = 0
    adf_result = adfuller(series)
    while adf_result[1] > 0.05 and d < 2:
        series = series.diff().dropna()
        adf_result = adfuller(series)
        d += 1
    return d

# Prepare lists to store results
results = []

# Parameter grid for ARIMA
p = q = range(0, 6)  # Expand p and q range up to 5
pdq = list(product(p, [0, 1, 2], q))

# Iterate through each file in the filtered directory
for filename in os.listdir(filtered_dir):
    if filename.endswith('.csv'):
        # Load the data
        file_path = os.path.join(filtered_dir, filename)
        df = pd.read_csv(file_path)

        # Convert Date column to datetime and sort by Date
        df['Date'] = pd.to_datetime(df['Date'])
        df = df.sort_values(by='Date').reset_index(drop=True)
        
        # Fill NaN in sentiment_score columns with zero
        sentiment_columns = [
            'sentiment_label_positive_count', 'sentiment_score_positive',
            'sentiment_label_negative_count', 'sentiment_score_negative',
            'sentiment_label_neutral_count', 'sentiment_score_neutral'
        ]
        df[sentiment_columns] = df[sentiment_columns].fillna(0)

        # Define features and target
        target = 'close'
        features_with_sentiment = ['open', 'volume'] + sentiment_columns
        features_without_sentiment = ['open', 'volume']

        # Prepare training and test datasets
        train_size = int(len(df) * 0.8)
        train, test = df[target][:train_size], df[target][train_size:]
        exog_train_with = df[features_with_sentiment][:train_size]
        exog_test_with = df[features_with_sentiment][train_size:]
        exog_train_without = df[features_without_sentiment][:train_size]
        exog_test_without = df[features_without_sentiment][train_size:]

        # Determine optimal differencing order d
        d_order = get_differencing_order(train)

        # Grid search for best SARIMAX parameters (with sentiment features)
        best_rmse_with = float("inf")
        best_order_with = None
        for param in product(range(6), [d_order], range(6)):  # Uses expanded p, d, q
            try:
                rmse, _ = evaluate_sarimax(train, test, exog_train=exog_train_with, exog_test=exog_test_with, order=param)
                if rmse < best_rmse_with:
                    best_rmse_with = rmse
                    best_order_with = param
            except:
                continue

        # Grid search for best SARIMAX parameters (without sentiment features)
        best_rmse_without = float("inf")
        best_order_without = None
        for param in product(range(6), [d_order], range(6)):  # Uses expanded p, d, q
            try:
                rmse, _ = evaluate_sarimax(train, test, exog_train=exog_train_without, exog_test=exog_test_without, order=param)
                if rmse < best_rmse_without:
                    best_rmse_without = rmse
                    best_order_without = param
            except:
                continue

        # Append results for this file
        results.append({
            'filename': filename,
            'best_rmse_with_sentiment': best_rmse_with,
            'best_order_with_sentiment': best_order_with,
            'best_rmse_without_sentiment': best_rmse_without,
            'best_order_without_sentiment': best_order_without
        })

# Display the results
results_df = pd.DataFrame(results)
print(results_df)


/Users/wenjing/miniforge3/envs/w210/lib/python3.9/site-packages/statsmodels/base/model.py:607: ConvergenceWarning: Maximum Likelihood optimization failed to converge. Check mle_retvals
  warnings.warn("Maximum Likelihood optimization failed to "
/Users/wenjing/miniforge3/envs/w210/lib/python3.9/site-packages/sklearn/metrics/_regression.py:492: FutureWarning: 'squared' is deprecated in version 1.4 and will be removed in 1.6. To calculate the root mean squared error, use the function'root_mean_squared_error'.
  warnings.warn(
/Users/wenjing/miniforge3/envs/w210/lib/python3.9/site-packages/statsmodels/base/model.py:607: ConvergenceWarning: Maximum Likelihood optimization failed to converge. Check mle_retvals
  warnings.warn("Maximum Likelihood optimization failed to "
/Users/wenjing/miniforge3/envs/w210/lib/python3.9/site-packages/sklearn/metrics/_regression.py:492: FutureWarning: 'squared' is deprecated in version 1.4 and will be removed in 1.6. To calculate the root mean squared error, 

/Users/wenjing/miniforge3/envs/w210/lib/python3.9/site-packages/statsmodels/base/model.py:607: ConvergenceWarning: Maximum Likelihood optimization failed to converge. Check mle_retvals
  warnings.warn("Maximum Likelihood optimization failed to "
/Users/wenjing/miniforge3/envs/w210/lib/python3.9/site-packages/sklearn/metrics/_regression.py:492: FutureWarning: 'squared' is deprecated in version 1.4 and will be removed in 1.6. To calculate the root mean squared error, use the function'root_mean_squared_error'.
  warnings.warn(
/Users/wenjing/miniforge3/envs/w210/lib/python3.9/site-packages/statsmodels/base/model.py:607: ConvergenceWarning: Maximum Likelihood optimization failed to converge. Check mle_retvals
  warnings.warn("Maximum Likelihood optimization failed to "
/Users/wenjing/miniforge3/envs/w210/lib/python3.9/site-packages/sklearn/metrics/_regression.py:492: FutureWarning: 'squared' is deprecated in version 1.4 and will be removed in 1.6. To calculate the root mean squared error, 

/Users/wenjing/miniforge3/envs/w210/lib/python3.9/site-packages/statsmodels/base/model.py:607: ConvergenceWarning: Maximum Likelihood optimization failed to converge. Check mle_retvals
  warnings.warn("Maximum Likelihood optimization failed to "
/Users/wenjing/miniforge3/envs/w210/lib/python3.9/site-packages/sklearn/metrics/_regression.py:492: FutureWarning: 'squared' is deprecated in version 1.4 and will be removed in 1.6. To calculate the root mean squared error, use the function'root_mean_squared_error'.
  warnings.warn(
/Users/wenjing/miniforge3/envs/w210/lib/python3.9/site-packages/statsmodels/base/model.py:607: ConvergenceWarning: Maximum Likelihood optimization failed to converge. Check mle_retvals
  warnings.warn("Maximum Likelihood optimization failed to "
/Users/wenjing/miniforge3/envs/w210/lib/python3.9/site-packages/sklearn/metrics/_regression.py:492: FutureWarning: 'squared' is deprecated in version 1.4 and will be removed in 1.6. To calculate the root mean squared error, 

/Users/wenjing/miniforge3/envs/w210/lib/python3.9/site-packages/statsmodels/base/model.py:607: ConvergenceWarning: Maximum Likelihood optimization failed to converge. Check mle_retvals
  warnings.warn("Maximum Likelihood optimization failed to "
/Users/wenjing/miniforge3/envs/w210/lib/python3.9/site-packages/sklearn/metrics/_regression.py:492: FutureWarning: 'squared' is deprecated in version 1.4 and will be removed in 1.6. To calculate the root mean squared error, use the function'root_mean_squared_error'.
  warnings.warn(
/Users/wenjing/miniforge3/envs/w210/lib/python3.9/site-packages/statsmodels/base/model.py:607: ConvergenceWarning: Maximum Likelihood optimization failed to converge. Check mle_retvals
  warnings.warn("Maximum Likelihood optimization failed to "
/Users/wenjing/miniforge3/envs/w210/lib/python3.9/site-packages/sklearn/metrics/_regression.py:492: FutureWarning: 'squared' is deprecated in version 1.4 and will be removed in 1.6. To calculate the root mean squared error, 

/Users/wenjing/miniforge3/envs/w210/lib/python3.9/site-packages/statsmodels/base/model.py:607: ConvergenceWarning: Maximum Likelihood optimization failed to converge. Check mle_retvals
  warnings.warn("Maximum Likelihood optimization failed to "
/Users/wenjing/miniforge3/envs/w210/lib/python3.9/site-packages/sklearn/metrics/_regression.py:492: FutureWarning: 'squared' is deprecated in version 1.4 and will be removed in 1.6. To calculate the root mean squared error, use the function'root_mean_squared_error'.
  warnings.warn(
/Users/wenjing/miniforge3/envs/w210/lib/python3.9/site-packages/statsmodels/base/model.py:607: ConvergenceWarning: Maximum Likelihood optimization failed to converge. Check mle_retvals
  warnings.warn("Maximum Likelihood optimization failed to "
/Users/wenjing/miniforge3/envs/w210/lib/python3.9/site-packages/sklearn/metrics/_regression.py:492: FutureWarning: 'squared' is deprecated in version 1.4 and will be removed in 1.6. To calculate the root mean squared error, 

...

/Users/wenjing/miniforge3/envs/w210/lib/python3.9/site-packages/sklearn/metrics/_regression.py:492: FutureWarning: 'squared' is deprecated in version 1.4 and will be removed in 1.6. To calculate the root mean squared error, use the function'root_mean_squared_error'.
  warnings.warn(
/Users/wenjing/miniforge3/envs/w210/lib/python3.9/site-packages/statsmodels/base/model.py:607: ConvergenceWarning: Maximum Likelihood optimization failed to converge. Check mle_retvals
  warnings.warn("Maximum Likelihood optimization failed to "
/Users/wenjing/miniforge3/envs/w210/lib/python3.9/site-packages/sklearn/metrics/_regression.py:492: FutureWarning: 'squared' is deprecated in version 1.4 and will be removed in 1.6. To calculate the root mean squared error, use the function'root_mean_squared_error'.
  warnings.warn(
/Users/wenjing/miniforge3/envs/w210/lib/python3.9/site-packages/statsmodels/base/model.py:607: ConvergenceWarning: Maximum Likelihood optimization failed to converge. Check mle_retvals
 

/Users/wenjing/miniforge3/envs/w210/lib/python3.9/site-packages/statsmodels/base/model.py:607: ConvergenceWarning: Maximum Likelihood optimization failed to converge. Check mle_retvals
  warnings.warn("Maximum Likelihood optimization failed to "
/Users/wenjing/miniforge3/envs/w210/lib/python3.9/site-packages/sklearn/metrics/_regression.py:492: FutureWarning: 'squared' is deprecated in version 1.4 and will be removed in 1.6. To calculate the root mean squared error, use the function'root_mean_squared_error'.
  warnings.warn(
/Users/wenjing/miniforge3/envs/w210/lib/python3.9/site-packages/statsmodels/base/model.py:607: ConvergenceWarning: Maximum Likelihood optimization failed to converge. Check mle_retvals
  warnings.warn("Maximum Likelihood optimization failed to "
/Users/wenjing/miniforge3/envs/w210/lib/python3.9/site-packages/sklearn/metrics/_regression.py:492: FutureWarning: 'squared' is deprecated in version 1.4 and will be removed in 1.6. To calculate the root mean squared error, 

/Users/wenjing/miniforge3/envs/w210/lib/python3.9/site-packages/statsmodels/base/model.py:607: ConvergenceWarning: Maximum Likelihood optimization failed to converge. Check mle_retvals
  warnings.warn("Maximum Likelihood optimization failed to "
/Users/wenjing/miniforge3/envs/w210/lib/python3.9/site-packages/sklearn/metrics/_regression.py:492: FutureWarning: 'squared' is deprecated in version 1.4 and will be removed in 1.6. To calculate the root mean squared error, use the function'root_mean_squared_error'.
  warnings.warn(
/Users/wenjing/miniforge3/envs/w210/lib/python3.9/site-packages/statsmodels/base/model.py:607: ConvergenceWarning: Maximum Likelihood optimization failed to converge. Check mle_retvals
  warnings.warn("Maximum Likelihood optimization failed to "
/Users/wenjing/miniforge3/envs/w210/lib/python3.9/site-packages/sklearn/metrics/_regression.py:492: FutureWarning: 'squared' is deprecated in version 1.4 and will be removed in 1.6. To calculate the root mean squared error, 

   filename  best_rmse_with_sentiment best_order_with_sentiment  \
0    BA.csv                 36.001251                 (0, 1, 0)   
1   MRK.csv                 16.870897                 (2, 1, 1)   
2  INTC.csv                  4.312688                 (3, 1, 1)   
3  MSFT.csv                 20.244528                 (1, 1, 1)   
4   AMD.csv                 16.681245                 (0, 1, 1)   
5  NVDA.csv                 35.003435                 (4, 1, 1)   
6  TSLA.csv                 15.390045                 (0, 1, 0)   
7  GOOG.csv                  2.404310                 (0, 1, 0)   
8  AAPL.csv                  5.973540                 (0, 1, 0)   

   best_rmse_without_sentiment best_order_without_sentiment  
0                    35.549648                    (0, 1, 0)  
1                    17.145411                    (1, 1, 0)  
2                     4.151028                    (0, 1, 3)  
3                    18.840076                    (1, 1, 1)  
4                  

/Users/wenjing/miniforge3/envs/w210/lib/python3.9/site-packages/statsmodels/base/model.py:607: ConvergenceWarning: Maximum Likelihood optimization failed to converge. Check mle_retvals
  warnings.warn("Maximum Likelihood optimization failed to "
/Users/wenjing/miniforge3/envs/w210/lib/python3.9/site-packages/sklearn/metrics/_regression.py:492: FutureWarning: 'squared' is deprecated in version 1.4 and will be removed in 1.6. To calculate the root mean squared error, use the function'root_mean_squared_error'.
  warnings.warn(


In [24]:
results_df

filename  best_rmse_with_sentiment best_order_with_sentiment  \
0    BA.csv                  3.169362                 (0, 0, 0)   
1   MRK.csv                  1.003401                 (4, 0, 4)   
2  INTC.csv                  0.691238                 (2, 0, 3)   
3  MSFT.csv                  4.168789                 (0, 0, 5)   
4   AMD.csv                  2.475428                 (3, 0, 5)   
5  NVDA.csv                  9.831670                 (4, 0, 5)   
6  TSLA.csv                  5.842376                 (4, 0, 3)   
7  GOOG.csv                  1.965512                 (3, 0, 3)   
8  AAPL.csv                  1.952407                 (0, 0, 2)   

   best_rmse_without_sentiment best_order_without_sentiment  
0                     3.109099                    (0, 0, 0)  
1                     1.009790                    (0, 0, 1)  
2                     0.713546                    (2, 0, 3)  
3                     4.248414                    (0, 0, 5)  
4                     2.484063                    (3, 0, 4)  
5                     9.873097                    (5, 0, 3)  
6                     5.982797                    (3, 0, 4)  
7                     1.680378                    (3, 0, 4)  
8                     1.867740                    (5, 0, 1)

In [25]:
import pandas as pd
import os

# Define the directory containing the CSV files
filtered_dir = '/Users/wenjing/Downloads/Capstone/filtered/'
output_dir = '/Users/wenjing/Downloads/Capstone/updated_filtered/'

# Ensure output directory exists
os.makedirs(output_dir, exist_ok=True)

# Iterate through each CSV file in the directory
for filename in os.listdir(filtered_dir):
    if filename.endswith('.csv'):
        # Load the CSV file
        file_path = os.path.join(filtered_dir, filename)
        df = pd.read_csv(file_path)

        # Calculate the return column as (close - open) / open
        df['return'] = (df['close'] - df['open']) / df['open']

        # Calculate the price_movement column: 1 if close > open, else 0
        df['price_movement'] = df['close'].gt(df['open']).astype(int)

        # Save the updated DataFrame to the output directory
        output_path = os.path.join(output_dir, filename)
        df.to_csv(output_path, index=False)

        print(f'Updated {filename} with return and price_movement columns.')


Updated BA.csv with return and price_movement columns.
Updated MRK.csv with return and price_movement columns.
Updated INTC.csv with return and price_movement columns.
Updated MSFT.csv with return and price_movement columns.
Updated AMD.csv with return and price_movement columns.
Updated NVDA.csv with return and price_movement columns.
Updated TSLA.csv with return and price_movement columns.
Updated GOOG.csv with return and price_movement columns.
Updated AAPL.csv with return and price_movement columns.


In [32]:
import pandas as pd
import numpy as np
import os
from statsmodels.tsa.statespace.sarimax import SARIMAX
from sklearn.metrics import mean_squared_error
from itertools import product

# Define paths
filtered_dir = '/Users/wenjing/Downloads/Capstone/updated_filtered/'

# Function to evaluate SARIMAX models
def evaluate_sarimax(train, test, exog_train=None, exog_test=None, order=(1, 1, 1)):
    model = SARIMAX(train, exog=exog_train, order=order, enforce_stationarity=False, enforce_invertibility=False)
    model_fit = model.fit(disp=False)
    predictions = model_fit.predict(start=len(train), end=len(train) + len(test) - 1, exog=exog_test)
    rmse = mean_squared_error(test, predictions, squared=False)
    return rmse, model_fit

# Prepare lists to store results
results = []

# Parameter grid for ARIMA
p = d = q = range(0, 6)
pdq = list(product(p, d, q))

# Iterate through each file in the filtered directory
for filename in os.listdir(filtered_dir):
    print(filename)
    if filename.endswith('.csv'):
        # Load the data
        file_path = os.path.join(filtered_dir, filename)
        df = pd.read_csv(file_path)

        # Convert Date column to datetime and sort by Date
        df['Date'] = pd.to_datetime(df['Date'])
        df = df.sort_values(by='Date').reset_index(drop=True)
        
        # Fill NaN in sentiment_score columns with zero
        sentiment_columns = [
            'sentiment_label_positive_count', 'sentiment_score_positive',
            'sentiment_label_negative_count', 'sentiment_score_negative',
            'sentiment_label_neutral_count', 'sentiment_score_neutral'
        ]
        df[sentiment_columns] = df[sentiment_columns].fillna(0)

        # Define features and target
        target = 'return'
        features_with_sentiment = ['open', 'volume'] + sentiment_columns
        features_without_sentiment = ['open', 'volume']

        # Prepare training and test datasets
        train_size = int(len(df) * 0.8)
        train, test = df[target][:train_size], df[target][train_size:]
        exog_train_with = df[features_with_sentiment][:train_size]
        exog_test_with = df[features_with_sentiment][train_size:]
        exog_train_without = df[features_without_sentiment][:train_size]
        exog_test_without = df[features_without_sentiment][train_size:]

        # Grid search for best SARIMAX parameters (with sentiment features)
        best_rmse_with = float("inf")
        best_order_with = None
        for param in pdq:
            try:
                rmse, _ = evaluate_sarimax(train, test, exog_train=exog_train_with, exog_test=exog_test_with, order=param)
                if rmse < best_rmse_with:
                    best_rmse_with = rmse
                    best_order_with = param
            except:
                continue

        # Grid search for best SARIMAX parameters (without sentiment features)
        best_rmse_without = float("inf")
        best_order_without = None
        for param in pdq:
            try:
                rmse, _ = evaluate_sarimax(train, test, exog_train=exog_train_without, exog_test=exog_test_without, order=param)
                if rmse < best_rmse_without:
                    best_rmse_without = rmse
                    best_order_without = param
            except:
                continue

        # Append results for this file
        results.append({
            'filename': filename,
            'best_rmse_with_sentiment': best_rmse_with,
            'best_order_with_sentiment': best_order_with,
            'best_rmse_without_sentiment': best_rmse_without,
            'best_order_without_sentiment': best_order_without
        })

# Display the results
results_df = pd.DataFrame(results)
print(results_df)


BA.csv


/Users/wenjing/miniforge3/envs/w210/lib/python3.9/site-packages/statsmodels/base/model.py:607: ConvergenceWarning: Maximum Likelihood optimization failed to converge. Check mle_retvals
  warnings.warn("Maximum Likelihood optimization failed to "
/Users/wenjing/miniforge3/envs/w210/lib/python3.9/site-packages/sklearn/metrics/_regression.py:492: FutureWarning: 'squared' is deprecated in version 1.4 and will be removed in 1.6. To calculate the root mean squared error, use the function'root_mean_squared_error'.
  warnings.warn(
/Users/wenjing/miniforge3/envs/w210/lib/python3.9/site-packages/statsmodels/base/model.py:607: ConvergenceWarning: Maximum Likelihood optimization failed to converge. Check mle_retvals
  warnings.warn("Maximum Likelihood optimization failed to "
/Users/wenjing/miniforge3/envs/w210/lib/python3.9/site-packages/sklearn/metrics/_regression.py:492: FutureWarning: 'squared' is deprecated in version 1.4 and will be removed in 1.6. To calculate the root mean squared error, 

/Users/wenjing/miniforge3/envs/w210/lib/python3.9/site-packages/statsmodels/base/model.py:607: ConvergenceWarning: Maximum Likelihood optimization failed to converge. Check mle_retvals
  warnings.warn("Maximum Likelihood optimization failed to "
/Users/wenjing/miniforge3/envs/w210/lib/python3.9/site-packages/sklearn/metrics/_regression.py:492: FutureWarning: 'squared' is deprecated in version 1.4 and will be removed in 1.6. To calculate the root mean squared error, use the function'root_mean_squared_error'.
  warnings.warn(
/Users/wenjing/miniforge3/envs/w210/lib/python3.9/site-packages/statsmodels/base/model.py:607: ConvergenceWarning: Maximum Likelihood optimization failed to converge. Check mle_retvals
  warnings.warn("Maximum Likelihood optimization failed to "
/Users/wenjing/miniforge3/envs/w210/lib/python3.9/site-packages/sklearn/metrics/_regression.py:492: FutureWarning: 'squared' is deprecated in version 1.4 and will be removed in 1.6. To calculate the root mean squared error, 

/Users/wenjing/miniforge3/envs/w210/lib/python3.9/site-packages/statsmodels/base/model.py:607: ConvergenceWarning: Maximum Likelihood optimization failed to converge. Check mle_retvals
  warnings.warn("Maximum Likelihood optimization failed to "
/Users/wenjing/miniforge3/envs/w210/lib/python3.9/site-packages/sklearn/metrics/_regression.py:492: FutureWarning: 'squared' is deprecated in version 1.4 and will be removed in 1.6. To calculate the root mean squared error, use the function'root_mean_squared_error'.
  warnings.warn(
/Users/wenjing/miniforge3/envs/w210/lib/python3.9/site-packages/statsmodels/base/model.py:607: ConvergenceWarning: Maximum Likelihood optimization failed to converge. Check mle_retvals
  warnings.warn("Maximum Likelihood optimization failed to "
/Users/wenjing/miniforge3/envs/w210/lib/python3.9/site-packages/sklearn/metrics/_regression.py:492: FutureWarning: 'squared' is deprecated in version 1.4 and will be removed in 1.6. To calculate the root mean squared error, 

/Users/wenjing/miniforge3/envs/w210/lib/python3.9/site-packages/statsmodels/base/model.py:607: ConvergenceWarning: Maximum Likelihood optimization failed to converge. Check mle_retvals
  warnings.warn("Maximum Likelihood optimization failed to "
/Users/wenjing/miniforge3/envs/w210/lib/python3.9/site-packages/sklearn/metrics/_regression.py:492: FutureWarning: 'squared' is deprecated in version 1.4 and will be removed in 1.6. To calculate the root mean squared error, use the function'root_mean_squared_error'.
  warnings.warn(
/Users/wenjing/miniforge3/envs/w210/lib/python3.9/site-packages/statsmodels/base/model.py:607: ConvergenceWarning: Maximum Likelihood optimization failed to converge. Check mle_retvals
  warnings.warn("Maximum Likelihood optimization failed to "
/Users/wenjing/miniforge3/envs/w210/lib/python3.9/site-packages/sklearn/metrics/_regression.py:492: FutureWarning: 'squared' is deprecated in version 1.4 and will be removed in 1.6. To calculate the root mean squared error, 

...

/Users/wenjing/miniforge3/envs/w210/lib/python3.9/site-packages/statsmodels/base/model.py:607: ConvergenceWarning: Maximum Likelihood optimization failed to converge. Check mle_retvals
  warnings.warn("Maximum Likelihood optimization failed to "
/Users/wenjing/miniforge3/envs/w210/lib/python3.9/site-packages/sklearn/metrics/_regression.py:492: FutureWarning: 'squared' is deprecated in version 1.4 and will be removed in 1.6. To calculate the root mean squared error, use the function'root_mean_squared_error'.
  warnings.warn(
/Users/wenjing/miniforge3/envs/w210/lib/python3.9/site-packages/statsmodels/base/model.py:607: ConvergenceWarning: Maximum Likelihood optimization failed to converge. Check mle_retvals
  warnings.warn("Maximum Likelihood optimization failed to "
/Users/wenjing/miniforge3/envs/w210/lib/python3.9/site-packages/sklearn/metrics/_regression.py:492: FutureWarning: 'squared' is deprecated in version 1.4 and will be removed in 1.6. To calculate the root mean squared error, 

/Users/wenjing/miniforge3/envs/w210/lib/python3.9/site-packages/statsmodels/base/model.py:607: ConvergenceWarning: Maximum Likelihood optimization failed to converge. Check mle_retvals
  warnings.warn("Maximum Likelihood optimization failed to "
/Users/wenjing/miniforge3/envs/w210/lib/python3.9/site-packages/sklearn/metrics/_regression.py:492: FutureWarning: 'squared' is deprecated in version 1.4 and will be removed in 1.6. To calculate the root mean squared error, use the function'root_mean_squared_error'.
  warnings.warn(
/Users/wenjing/miniforge3/envs/w210/lib/python3.9/site-packages/statsmodels/base/model.py:607: ConvergenceWarning: Maximum Likelihood optimization failed to converge. Check mle_retvals
  warnings.warn("Maximum Likelihood optimization failed to "
/Users/wenjing/miniforge3/envs/w210/lib/python3.9/site-packages/sklearn/metrics/_regression.py:492: FutureWarning: 'squared' is deprecated in version 1.4 and will be removed in 1.6. To calculate the root mean squared error, 

/Users/wenjing/miniforge3/envs/w210/lib/python3.9/site-packages/statsmodels/base/model.py:607: ConvergenceWarning: Maximum Likelihood optimization failed to converge. Check mle_retvals
  warnings.warn("Maximum Likelihood optimization failed to "
/Users/wenjing/miniforge3/envs/w210/lib/python3.9/site-packages/sklearn/metrics/_regression.py:492: FutureWarning: 'squared' is deprecated in version 1.4 and will be removed in 1.6. To calculate the root mean squared error, use the function'root_mean_squared_error'.
  warnings.warn(
/Users/wenjing/miniforge3/envs/w210/lib/python3.9/site-packages/statsmodels/base/model.py:607: ConvergenceWarning: Maximum Likelihood optimization failed to converge. Check mle_retvals
  warnings.warn("Maximum Likelihood optimization failed to "
/Users/wenjing/miniforge3/envs/w210/lib/python3.9/site-packages/sklearn/metrics/_regression.py:492: FutureWarning: 'squared' is deprecated in version 1.4 and will be removed in 1.6. To calculate the root mean squared error, 

   filename  best_rmse_with_sentiment best_order_with_sentiment  \
0    BA.csv                  0.015702                 (0, 0, 0)   
1   MRK.csv                  0.010730                 (0, 0, 1)   
2  INTC.csv                  0.021518                 (5, 0, 2)   
3  MSFT.csv                  0.012360                 (4, 0, 5)   
4   AMD.csv                  0.026289                 (4, 0, 4)   
5  NVDA.csv                  0.024608                 (5, 0, 1)   
6  TSLA.csv                  0.024332                 (5, 0, 5)   
7  GOOG.csv                  0.014928                 (0, 0, 2)   
8  AAPL.csv                  0.011159                 (0, 0, 2)   

   best_rmse_without_sentiment best_order_without_sentiment  
0                     0.015429                    (0, 0, 0)  
1                     0.010806                    (0, 0, 1)  
2                     0.021945                    (0, 0, 1)  
3                     0.012524                    (4, 0, 4)  
4                  

/Users/wenjing/miniforge3/envs/w210/lib/python3.9/site-packages/statsmodels/base/model.py:607: ConvergenceWarning: Maximum Likelihood optimization failed to converge. Check mle_retvals
  warnings.warn("Maximum Likelihood optimization failed to "
/Users/wenjing/miniforge3/envs/w210/lib/python3.9/site-packages/sklearn/metrics/_regression.py:492: FutureWarning: 'squared' is deprecated in version 1.4 and will be removed in 1.6. To calculate the root mean squared error, use the function'root_mean_squared_error'.
  warnings.warn(
/Users/wenjing/miniforge3/envs/w210/lib/python3.9/site-packages/statsmodels/base/model.py:607: ConvergenceWarning: Maximum Likelihood optimization failed to converge. Check mle_retvals
  warnings.warn("Maximum Likelihood optimization failed to "
/Users/wenjing/miniforge3/envs/w210/lib/python3.9/site-packages/sklearn/metrics/_regression.py:492: FutureWarning: 'squared' is deprecated in version 1.4 and will be removed in 1.6. To calculate the root mean squared error, 

In [33]:
results_df

filename  best_rmse_with_sentiment best_order_with_sentiment  \
0    BA.csv                  0.015702                 (0, 0, 0)   
1   MRK.csv                  0.010730                 (0, 0, 1)   
2  INTC.csv                  0.021518                 (5, 0, 2)   
3  MSFT.csv                  0.012360                 (4, 0, 5)   
4   AMD.csv                  0.026289                 (4, 0, 4)   
5  NVDA.csv                  0.024608                 (5, 0, 1)   
6  TSLA.csv                  0.024332                 (5, 0, 5)   
7  GOOG.csv                  0.014928                 (0, 0, 2)   
8  AAPL.csv                  0.011159                 (0, 0, 2)   

   best_rmse_without_sentiment best_order_without_sentiment  
0                     0.015429                    (0, 0, 0)  
1                     0.010806                    (0, 0, 1)  
2                     0.021945                    (0, 0, 1)  
3                     0.012524                    (4, 0, 4)  
4                     0.026488                    (2, 0, 2)  
5                     0.022762                    (1, 0, 4)  
6                     0.024955                    (3, 0, 4)  
7                     0.014580                    (1, 1, 1)  
8                     0.010420                    (5, 0, 1)

In [9]:
from datetime import datetime
import pytz

# Define the UTC datetime
utc_time = datetime.strptime("2023-12-16 21:00:00", "%Y-%m-%d %H:%M:%S")

# Set the timezone to UTC
utc_zone = pytz.timezone('UTC')
utc_time = utc_zone.localize(utc_time)

# Convert to Eastern Time (EST/EDT)
eastern_zone = pytz.timezone('US/Eastern')
est_time = utc_time.astimezone(eastern_zone)

print("UTC time:", utc_time)
print("Eastern Time:", est_time)


UTC time: 2023-12-16 21:00:00+00:00
Eastern Time: 2023-12-16 16:00:00-05:00


In [34]:
import pandas as pd
import numpy as np
import os
import pickle
from statsmodels.tsa.statespace.sarimax import SARIMAX
from sklearn.metrics import mean_squared_error
from itertools import product

# Define paths
filtered_dir = '/Users/wenjing/Downloads/Capstone/filtered_combined_decay_score_with_returns/'
model_save_dir = '/Users/wenjing/Downloads/Capstone/saved_models/'  # Directory to save models

# Ensure the model save directory exists
os.makedirs(model_save_dir, exist_ok=True)

# Function to evaluate SARIMAX models
def evaluate_sarimax(train, test, exog_train=None, exog_test=None, order=(1, 1, 1)):
    model = SARIMAX(train, exog=exog_train, order=order, enforce_stationarity=False, enforce_invertibility=False)
    model_fit = model.fit(disp=False, method='powell', maxiter=500)
    predictions = model_fit.predict(start=len(train), end=len(train) + len(test) - 1, exog=exog_test)
    rmse = np.sqrt(mean_squared_error(test, predictions))
    return rmse, model_fit

# Prepare lists to store results
results = []

# Parameter grid for ARIMA
p = d = q = range(0, 3)
pdq = list(product(p, d, q))

# Iterate through each file in the filtered directory
for filename in os.listdir(filtered_dir):
    if filename.endswith('.csv'):
        print(f"Processing {filename}")
        # Load the data
        file_path = os.path.join(filtered_dir, filename)
        df = pd.read_csv(file_path)

        # Extract stock symbol from filename (assuming format like 'AAPL.csv')
        stock_symbol = filename.split('.')[0]

        # Convert Date column to datetime and sort by Date
        df['Date'] = pd.to_datetime(df['Date'])
        df = df.sort_values(by='Date').reset_index(drop=True)
        
        # Fill NaN in sentiment_score columns with zero
        sentiment_columns = ['weighted_sentiment_score']
        df[sentiment_columns] = df[sentiment_columns].fillna(0)

        # Define features and target
        target = 'return'
        features_with_sentiment = ['open', 'volume'] + sentiment_columns

        # Prepare training and test datasets
        train_size = int(len(df) * 0.8)
        train, test = df[target][:train_size], df[target][train_size:]
        exog_train_with = df[features_with_sentiment][:train_size]
        exog_test_with = df[features_with_sentiment][train_size:]

        # Grid search for best SARIMAX parameters (with sentiment features)
        best_rmse = float("inf")
        best_order = None
        best_model = None
        for param in pdq:
            try:
                rmse, model_fit = evaluate_sarimax(train, test, exog_train=exog_train_with, exog_test=exog_test_with, order=param)
                if rmse < best_rmse:
                    best_rmse = rmse
                    best_order = param
                    best_model = model_fit
            except Exception as e:
                print(f"Error with params {param}: {e}")
                continue

        # Save the best model for this stock
        if best_model:
            model_save_path = os.path.join(model_save_dir, f"{stock_symbol}_sarimax_model.pkl")
            with open(model_save_path, 'wb') as f:
                pickle.dump(best_model, f)
            print(f"Saved model for {stock_symbol} to {model_save_path}")

        # Append results for this stock
        results.append({
            'stock_symbol': stock_symbol,
            'best_rmse': best_rmse,
            'best_order': best_order
        })

# Save the results to a CSV file
results_df = pd.DataFrame(results)
results_df.to_csv(os.path.join(model_save_dir, 'model_results.csv'), index=False)
print("Model results saved.")


Processing BA.csv
Saved model for BA to /Users/wenjing/Downloads/Capstone/saved_models/BA_sarimax_model.pkl
Processing MRK.csv
Saved model for MRK to /Users/wenjing/Downloads/Capstone/saved_models/MRK_sarimax_model.pkl
Processing INTC.csv
Saved model for INTC to /Users/wenjing/Downloads/Capstone/saved_models/INTC_sarimax_model.pkl
Processing MSFT.csv
Saved model for MSFT to /Users/wenjing/Downloads/Capstone/saved_models/MSFT_sarimax_model.pkl
Processing AMD.csv
Saved model for AMD to /Users/wenjing/Downloads/Capstone/saved_models/AMD_sarimax_model.pkl
Processing NVDA.csv
Saved model for NVDA to /Users/wenjing/Downloads/Capstone/saved_models/NVDA_sarimax_model.pkl
Processing TSLA.csv
Saved model for TSLA to /Users/wenjing/Downloads/Capstone/saved_models/TSLA_sarimax_model.pkl
Processing GOOG.csv
Saved model for GOOG to /Users/wenjing/Downloads/Capstone/saved_models/GOOG_sarimax_model.pkl
Processing AAPL.csv
Saved model for AAPL to /Users/wenjing/Downloads/Capstone/saved_models/AAPL_sari